# Histopathologic Cancer Detection

This project tries to construct a deep learning model(based on a convolutional neural network) to identify metastatic tissue in histopathologic scans of lymph nodes.

i use transfer learning from a pre-trained model Xception and MObileNetV2. Then using the Global Average Pooling function on the result from each pre-train model, and then concatenate the pooled result for the final presentation.

The different combinations of the pre-trained model can be selected to find the most appropriate ensemble combination. 

The computational cost of this training is very high, so it should be run on the GPU or Kaggle notebook. 

## Dataset

The dataset is a slightly modified version of the PatchCamelyon benchmark dataset. 

It can be downloaded here: https://www.kaggle.com/c/histopathologic-cancer-detection/data

## import all required libraries

In [1]:
import numpy as np 
import pandas as pd 
import matplotlib.pyplot as plt
%matplotlib inline
from glob import glob 
import cv2
from skimage.io import imread 
import os
import shutil
from sklearn.metrics import roc_curve, auc, roc_auc_score
from sklearn.model_selection import train_test_split
from keras.preprocessing.image import ImageDataGenerator
from keras.applications.nasnet import NASNetMobile
from keras.applications import MobileNetV2
from keras.applications.xception import Xception
from keras.utils.vis_utils import plot_model
from keras.layers import Dropout, Flatten, Dense, GlobalAveragePooling2D, Average, Input, Concatenate, GlobalMaxPooling2D
from keras.models import Model
from keras.callbacks import CSVLogger, ModelCheckpoint
from keras.optimizers import Adam
from livelossplot import PlotLossesKeras

In [2]:
!pip install livelossplot

## Data Exploration

In [3]:
#create a dataframe of train image labels
path = "C:/Users/super/OneDrive - The University of Tokyo/Data Science portfolio/Histopathologic-Cancer-Detection-main/train_labels.csv"
df = pd.read_csv(path)
print('Shape of DataFrame',df.shape)

df.head()

Shape of DataFrame (220025, 2)


id  label
0  f38a6374c348f90b587e046aac6079959adf3835      0
1  c18f2d887b7ae4f6742ee445113fa1aef383ed77      1
2  755db6279dae599ebb4d39a9123cce439965282d      0
3  bc3f0c64fb968ff4a8bd33af6971ecae77c75e08      0
4  068aba587a4950175d04c680d38943fd488d6a9d      0

## Feature engineering


In [6]:
# take a sample size of 85000 to avoid crashing
SAMPLE_SIZE = 85000

# take a random sample of class 0 with size equal to num samples in class 1
df_0 = df[df['label'] == 0].sample(SAMPLE_SIZE, random_state = 0)
# filter out class 1
df_1 = df[df['label'] == 1].sample(SAMPLE_SIZE, random_state = 0)

# concat the dataframes
df_train = pd.concat([df_0, df_1], axis = 0).reset_index(drop = True)

# shuffle
df_train.sample(frac=1)

df_train['label'].value_counts()

0    85000
1    85000
Name: label, dtype: int64

In [7]:
df_train.head()

id  label
0  4d03f037381aa81370f4ef724cece830910be6e2      0
1  fe6129053d73422aa1c3ba03b41deacf68d2d27b      0
2  dd752745021474b0752095c8d6c8af72ea9f40ea      0
3  514deb337e49c9ba0cc3d20f990b47799059c72c      0
4  4a20631d20270b4b5e97eaeeba85e9b7f09337af      0

In [8]:
df_train.tail()

id  label
169995  465a70e648cd5f414e584798d349f603a584980e      1
169996  d1a0ca789344beabd2e4c7f26a3f0ec6251daf98      1
169997  970530056fad2be4b994d07f3142317a3bc65986      1
169998  05ce96e76de1558ada854e01ac6a0f5a926c04f6      1
169999  3b3cded61e61f33b91bdfa0a9aab73f6ad0da7be      1

In [9]:
# split into training and validation sets
y = df_train['label']
df_train, df_val = train_test_split(df_train, test_size = 0.1, random_state = 0, stratify = y)

In [10]:
# Create a new directory
b_dir = 'b_dir'
os.mkdir(b_dir)


# create a path to 'b_dir' to which we will join the names of the new folders
# trn_dir
trn_dir = os.path.join(b_dir, 'trn_dir')
os.mkdir(trn_dir)

# v_dir
v_dir = os.path.join(b_dir, 'v_dir')
os.mkdir(v_dir)

# create new folders inside trn_dir
neg = os.path.join(trn_dir, '0')
os.mkdir(neg)
pos = os.path.join(trn_dir, '1')
os.mkdir(pos)


# create new folders inside v_dir
neg = os.path.join(v_dir, '0')
os.mkdir(neg)
pos = os.path.join(v_dir, '1')
os.mkdir(pos)

print(os.listdir('b_dir/trn_dir'))
print(os.listdir('b_dir/v_dir'))


['0', '1']
['0', '1']


In [30]:
# check the label 
df[df['id']=='34edae3b57440c40ada8aa92da2f242df5a5898b']['label'].values[0]

0

In [34]:
# Get a list of train and val images
train_list = list(df_train['id'])
val_list = list(df_val['id'])
for image in train_list:
    print(image)
    # the id in the csv file does not have the .tif extension therefore we add it here
    file_name = image + '.tif'
    # get the label for a certain image
    target = df[df['id']==image]['label'].values[0]
    # these must match the folder names
    if target == 0:
        label = '0'
    elif target == 1:
        label = '1'
    
    # source path to image
    src = os.path.join("C:/Users/super/OneDrive - The University of Tokyo/Data Science portfolio/Data_Hispathology/train", file_name)
    # destination path to image
    dest = os.path.join(trn_dir, label, file_name)
    # copy the image from the source to the destination
    shutil.copyfile(src, dest)

34edae3b57440c40ada8aa92da2f242df5a5898b
31fae644b8e8a58aa5274d3ffe85a8d58a4e8bff
39b7aa1a63a10c995871c02a569bbb37b4d2d4c1
04a6acbea83b829c66796b26a55c5b4b3c8af797
7ef1ea5b99629afbbe6e8a2b4df4655386bf5d29
6e6fce2375ed3cdc5daf65fbfc49241f65e26461
a229c5e791ba3d43c234e828425ef7f3501ef7bf
acde1d174cb3c94169f634ab178f56a25c7a070b
f621b8cf781431031e5eef1087e553e2c5e0acf5
4bf98d34eac2684b64f0855fcf30e419fce56c6b
d2ae125ca257e2f67eb5927d5a5fbf88002ca11f
76a0988b6d17669690c1e08a1b0236a91c77daa7
87c07b3192257fcc9f5cdd1ca83f8ba4ac752e8f
11dae5b9001f9482732bfb7ba805be77a250e5de
ef11d1b189672b02413b8e9e78d6db44bd464184
1a7c01c42f96c851975b20a1dec05db3b011bc36
62b00f70d34e88a1d248b0e8af17e10f93ed0889
cb0fa6efe7cab5b51b45010e3906e886aacdef00
96c63d2443d926d2108f1c7086885353aa5cf27b
0d4906ceaba66e13d33f8a432541d28b1d0a0ad2
f47ea3b0a60d42358a28b968795c93418dd6d79a
bf124688a25275dd28defb9419a14e6d80c1bd74
fb17e73d023f2892cf622c86b9ace49c5ed1be2c
f0dae8efd53c868da85f49fc12ce81c3062eac4d
4e210c1ed8e1f02e

ee06c9959e01b857e657154bba616943587c58b3
247b9666ceae8921a655ab4af004a601fa5c50ef
1d1371074dc25277a22b1518627c469ccea5e582
6d4a0f9936f275dceef5d8730e8e5d1d814d234a
104f467697a2d6c992dd16090ae6651b86c5fb35
fe520665f21f76336f312f8f68bcd4831c057dd5
73c0dbdb147bfe540fa9e621301142d9ba21fcd3
3d8962cec54460c8988f763383b0c4644429ddf6
8c708dd219427cfecf858b8d1a8a8d2f8a0d8f2b
7026751602ffb6d25a74bb2d0183ed300c894725
fe079edd37ecf855831398e117c8e7f16b8fe229
b91f95df684d6eb696c97caf2c2da0f53d8440ee
ea24a1781b88197c89fda756dea9ceb74253b04f
fe963efbb78f9aeac660e8590443c7c15010ddc5
40c42115cc586e7a2e53dfa22d497cf2adb4a51c
bd4a42624f1fcf61082e2eac57efcc7505db440a
4ea546391337dbf9dab8ae1cfb20ff3d548e6448
6af42f2b398c9184d8882c6581210a38c01fdcec
5f50e5745dc41dc25d23ff5d90abf224ee59f723
b497df83ae06d838c7c0f06095c4f486f28a8a35
bd388b9406124ebac5929a6d2be59e520028747f
ce17a205761448d6b7913fa160b81b61aab066f3
43bedf06ffec2c86f798e4e91cd29cb513c2588c
d9644995b895d24eb353ff23bec4c544c5f64a74
7ad57a8ea473d15d

74d90bfa50fd2ecda8eb5e8bd60e32ac1dcbf127
a280f97cf9df15756f36f517e1294ee5dd959425
ea6b60983d2b1b762b51e57d345c070aaac4f718
604a0350432a3274192c5f97786df73300ea8fc7
58195b10b8e5de167ba169c61c8dd2645cc2b612
0b92fcda3ae2de7ac728ca464d4f72ba64eefe78
793597e62a01f8bb9bcf3e56c4b2e30bf1934822
f63d92bd5fff512f93945daeb5d0bda39212132f
d5f1a72fa38a54d60959cefc62a9ac75e3d82da7
5df6f1bdd1eb985fbfaed5bcaf043917e2a124dc
cf60d4a7300015b62241cdcd10800bd2ae251400
4e759960f20beda4ee6f64d41c5886f1a097fc1f
c65a4d5ddacb6adf6cfe31e5eed70f63cb2e1941
3d0c8d70c5fe39093477c9f06cd661788642238b
af0c61eb86a73931daafba85339d1b97caa5c7a2
73d44bb19808d90dc39a4552988bf2a561bf0254
6e574261402e968ebcdf7640989c91c10a236172
f949c119adb88e97ffe5c7a6aefeaad51bdb9d92
015df4156746e9f351cf393eb61ef2d184b0a927
abf0c5b7bf9f3e228378903ede0788b5bd4ae307
0aa4f67a48050cd54a27bff91edd14ac5dc547a2
1e078611a79ac1c8390512bf2b56584abd3141d7
43d732ea1da8adef9516146bb29007297560d899
c0ababce90664c39b7ccc1ba90cea7fb90f41b85
7cbd431b7021ce1a

f93179749ab0999236ef3b95661c430313087f84
72de5b58fc5bcfdf07c635f9272010e6a9d3d9b9
46290edbdce813caa0ae8de0ecf06710eac188b1
6eb578c23e0045bc246bd131c6192cdb07977d3a
b23cb826fbad4a588f6997ccfc4a4ed614c18646
5887aac77b26b7339b7ad331e0ef9fa934c02867
00440e6fecac3f22c5e61d1a842cc59058161f91
0eea1bfe74cecdb5c0aba3a838aea3bf07374982
8224aa144fb4b89734ab037f8ec8a8c9c634d871
f8c6f70e379b7cf366cf865861bd5f860824adf9
6961bdcc16f6c1d7db88fc6a7823178288c2a29e
1660534388bef8a6ee112c8c09bb252a6b8540ed
fe1a02f0f7602674c3295c82f1f6a0b3edbb361b
c6108bc8d98df27748861e7b6c220764058c38fe
9adcec64b1991cf6594525b3be346103d93f11af
0972a444b392c013f39328e96e7a7cd57bbae5a7
f330a897b0215ae8b972834bcea59682c6114a66
ef5de8780091a0ed37ffeed91175d4458420aa6f
1c706b882acc5b3054cd1762146bd046dc517eb7
22763dd7ab3b8222495e23ae5121707ec7ec447c
b00a2a4ed2a1164a196c9768c16784f86c35b30d
118f3f78e490425d15998a7233360e1ab8507b2e
e9fbf83741e1a4da716ac5b959d0564117d526f0
ecec05268a2117ccb754e23367aa9dd86d3c3591
e6756e8e952b69be

2bf6e7f62eb4e75694e6c47bbceea07f8dd6cdbf
9f0857483fc70630430cb4411b51f591e2d023bd
9f4af5a394873b176acc15718d0afef4c842bd96
ae618c91772987688a842b0f261eff1fd6e958b8
4dce5dce242b56d7d79240b438e47d916d355f5f
c03c8ec6e289fd79f662f82f20cbb74681ba37bf
e359838cf1e8c777a2706ce1f9aaf10edd1667a9
82d7e666005259912b9f9e669a0117f4dbff3e8c
fc32f6d9d7cd6416dc3dad054923e6e013da8b38
eb285d5acdbeaa490b281a36af771d53d7ba073c
424e34cb2f5ecc042c830756dcde5f10337ed4cd
9a2475f88982fa07ba587592d4097eafd83a3c2b
ae2684392353844449a84873baa72c5e724606ba
e52bb37d583ce1376e82bde9fa47dc2cfa6afa28
a1c02927b06030adb139dcef6ad28d7d1f9a3f59
3ceab94c423caecd6ccfce426059782e581f0168
074530dd6c0e8adf88a9c61d0a20cd148e01caab
f5c19d6ef61d506005733c503c842a929985db70
159a17767884913451f4e5b0a6b5f0c8ff223c0d
ad7b760481a8d490809a74a8017c07e5755bfe5b
ab4478fe874d0371382763a1982132d2d0dcadb1
94ff74c0e7333f66183f459f7b6130ad6c56ad68
5bf93f063b00382ee2b455059d543456508afab0
745ed6c1b07b0128d03af602526d1cdf83157536
deae57514c59abeb

...

1f1e6a9130d65e41c278e30d4e39adaf81c332a6
747ee95f8888b9757159f26fea22cfb9af7d8c17
b20b8fbdff40ed456e89173850a14eb71ecdbb77
25c5a8876bdb5e64690a020f5374c857a581c22d
2f395d44918155b0373f110ceade7c715f1dfbda
55e0ea899de6e741ad0ac4398b025b1d156aede4
29b8e3ec8f3468063c1f03ce135aaf474b99921a
e848dcce6c7e4cde47bb823c9dd0a4bce56be800
6165b12b516d9920f71d4533886ccbd43f67a386
3eb2716a60b25ef43db7c2c424d8d02790c04174
2f4d6cba729b3021cee187e265a03cb215411285
bb1517ab0551fbe033c73e78c1cc23026f4226a9
83a14aa9a60e4def439d2b702e0f599ba0789f76
74bd7373311986b58a9d722828fe777ef7a1c205
047f57a63a90f86a6b1f18a7968f8a9292b268ec
ab80d2f63b82c4d88ae48477deffcbafc72aec69
10ed0d7f2ba481625f71a23dc340ac3f0c090575
cd56e1662080d41bf13632e4f01755fbef7ad3a7
a9b5692d4e573734385575966d2eb82d73de919b
ce6507e5ba042c463c07ba81d51dd3e320a1fbe6
0d03cad539ed4d42a8e578e8b880516ff6f51e56
3bcd0541becf538e59bc74d55ada9f3cfe07208d
8aa91a7f6c6c1711e7fd1605d0946670ae2ec8c2
c58275b822db8eb2a4e87de7cf0da5f304f36334
f9659f70a7df8887

def9d99f89c7c59624020744a5160ef9a621b2a6
5deb4d1d352d821bc553b009aae5f66a5531e49d
baf49c111906d2d148e26c8dff1bee04a04a6752
f2a6f359d6fd48b9c087b464e0c38374acb6759f
371092e426a652b682d8eea1e2a15620ff798661
bd06fb67194d257e84bd5b795eb4c8e811c6cb19
1f1cdcd0a5be5d10615ead91ffda725d9e62f083
daf49fc029043d6416030412364d186941c9716c
fb4319e26cd920f095a1ced1288bd04e2bb54167
3e1cce335c2a45e95e64b667873a4ba35fb73edb
a2db573dbb25bc5278f9d33dabb1fcc343dbe80a
2c6c9565d87c45ffdabb505b1e833dcb6288782d
a20c4066477e123467392ac93c1b2053b50172ca
ee4bec1c8037cb19f1f22967e0f704d99056b11c
3bc21cb71ad3363b8b5f042f8ca9cf4462547ee4
755674ccbd0d0a6ee65b3063e083b3147ddd672b
5a02a356dbd720c4ee1c2d427538a5751dd04d86
6a543d33eac1207d0137ae623979b8a8156ae2d5
7619896ca60523af42ddd6cd7737edfb16c6d3c4
6504657b19259c85d35a8cce330c799e887a8f41
4fabc24406fc758e7555460be618923efc061392
64e23f41247318bb5d10faedc5c4155219e36795
5b3af7344fe31c285f541b08cb4cbcd7de048e94
fe9b279294b11c37202f6789893813c7cb02ebb7
a97abceb297e42d6

3ded5e97ea73598969e3cdd00ec2b448bbf4fbad
060c71a1ea173019777916dc5d642f30c94f09ed
a17dd4743a42e1b35ee87481f9b65f37be0aff14
d043abdf23717faba2baafe4bb169a142598d6d0
e6bb527faa491d24df1e49f74debb848eebc98ce
d9aa0bb62a9daaf7e5846b7a7b26dcde37a33ff9
e2b158905fef9ae4f727f95f07c0fed9a998c75d
e3a2e3ad762c107a1305d27c67bf3f507d4f7ba6
530999a6ef541588b74f45d778e2e338f2a0f50c
b8758f7fd7723abc117b72f82ccd878cac668c3e
a6888bdfa536bf87d9b76905e72c191f97d159fc
5e310b95430ebaaaef09c7909bd931c682d0e78b
16c79254da1f8720dd495c2c20bc8a0b15c27ee1
02d7c3fc5b2601b0201062df6ca1402324c2b246
5dd194e446d52921cb462c76ae0054be0fa02497
080040be2936935bc9f5ad201e2883538d9efcaf
52f91922d239f621c5b5bf4452f6873b56c5bc22
4cbc9c4e57ca997d3224ff5c549a53fce9da721d
d93d0d5de1b9f1f96570f8cbb6ce1510ab70af6b
11c163b7d54478c366944fb9988ccdd32201b15b
dbdbef9af2340bf61b9804ca38732327a747e4a1
5f34ea15d2be5835dc2b7b56ed89572d3e44633e
eb440204d7ee7d473339fcde8aa3cc054b100c74
fbfe8e8ba34baf479ebc460862d2e82a69ffddba
c0ee8a3c293814c3

cc6a3d3f3332b69db55985c86cc5ed12a5d95994
49961eb12d563006caf7442f8bcae7055c69fa24
4719c8bb0102a38f58dc12ab54c130202a29128f
d29452ddd54a808f48e33b11e5290c5a78f6c2ed
5b37c166b0bb4fe875e29c70e0ec539a2cdc4beb
99ac54a0fae06231d10539ae269ed3c00c79a99a
76f1b2fce62ff5fc5ea534560464520cf4e136d7
dcbb647e68ec8b6738776a23c18511fb711761ef
5b23281809466d1f24b7a634238faf5af0146d8d
026c786bff59ee7a0c98ab0d12af639547b81ef3
52b901490e4bcbbe977d3516311500e61842ecb0
964dc925b117f2607529a553a9ba1129b0ee74b2
5e825122ab2f3a0eb266ecfc9b61613c202bdb3e
18af9ea0994f68f96a8a0a94f1c08804346526c3
2d7030f82c0c1f71455fa9cc22f42c4f8dc3430e
3089abffcd1d70dd3cda629b42ecaef760412f40
21a9fe2bc99fd0f78e2a3cbfabe57e65e70b68fd
4bd87d2b2f554a624569c57f6805f08ec06f3da5
f4dff6596ef8fedc21ed69e228393dc38871431c
fc67ee8950da86587d06e5299298d09b450bbb1a
107df7303880bd4cad40e2e5a78e5f3f6c25ec33
9ed7d8cc2eacce39dba0b6061038dc750d0cb1ec
75d94322273776a6a7513b9dd5c3e94e3ef491fb
6b73f1939cdebf54f20ffafb1c75d17b426cdf62
8fbb48b23625a8b4

fc235c93d4821c104bedf31a79bb109c50287262
f5681bdd233e9ec2bcef246a848ef429acd41cba
bc8ba3513a15ed6aac43b08f641346906f3c0131
89f5196aa04576c13bf41e69fbb249a28c842c08
9c97c023d15b54091b39429345780f24cdab7894
9e98180732fba4e74adad8a5098a16c47ee55a81
4ed8858c902f352c2a6aa781b1ef6e32fec7d2dd
2897a8009500854712b8811d91df70c83851ef32
b5e0098fd0a47f1e5f91d8fffdbde27c44e7ba0e
51ddda8946d748f7da1984e2d5707bbc3be7f0d3
7c71d3a26e829d5f7ed7d8c6d7295da39df4c5f1
41c27aa16e80159d85e2f65105b791a05cb83dc6
8a78ff24e014cfa95754f18193253d2bc8b9b152
7e6014021f39f6fbad8599350355d3d83336cd17
62c59c7a4ab7092e7bf9ede9592072d6401c7991
68ad61b2685842694f718dfd587e609da9409b7e
b43c34589da0a5be6905e7e7cb81c73a3f2d5b60
ff3d24bad0fddbfb784ebe4f2564a92f517991ac
dce3a4fb4207e96c49c15b5e78817989b02fa2b5
d1a6b5ed4429d1186b7da791c4f31221e55fe4af
491a8e0d0831a9185559c5618d4334061579bbf7
0b9ae6d138e64eac2fa0ebbdc3109cbf575f2aec
b2e7217d02d9ed90a53524c790cc74683bd0a63b
df3d7dd1488d637e6b681523c13465588caef2d7
73e23354734da356

In [36]:
# do the same process for the validation set 
for image in val_list:
    
    # the id in the csv file does not have the .tif extension therefore we add it here
    file_name = image + '.tif'
    # get the label for a certain image
    target = df[df['id']==image]['label'].values[0]
    
    # these must match the folder names
    if target == 0:
        label = '0'
    elif target == 1:
        label = '1'
    

    # source path to image
    src = os.path.join("C:/Users/super/OneDrive - The University of Tokyo/Data Science portfolio/Data_Hispathology/train", file_name)
    # destination path to image
    dest = os.path.join(v_dir, label, file_name)
    # copy the image from the source to the destination
    shutil.copyfile(src, dest)

In [39]:
print(len(os.listdir('b_dir/trn_dir/0')))
print(len(os.listdir('b_dir/trn_dir/1')))

124008
76500


## Data Augmentation

In [37]:
# Perform Data augmentation
data_augmentation = ImageDataGenerator(rescale=1./255,
                                       horizontal_flip=True,
                                       vertical_flip=True,
                                       rotation_range=180,
                                       zoom_range=0.4, 
                                       width_shift_range=0.3,
                                       height_shift_range=0.3,
                                       shear_range=0.3,
                                       channel_shift_range=0.3)

In [40]:
batch_size = 192
image_size = 96

train_path = 'b_dir/trn_dir'
val_path = 'b_dir/v_dir'
test_path = '"C:/Users\super/OneDrive - The University of Tokyo/Data Science portfolio/Data_Hispathology/test"'

train_set = data_augmentation.flow_from_directory(train_path,
                                                            target_size = (image_size,image_size),
                                                            batch_size = batch_size,
                                                            class_mode = 'binary')
val_set = ImageDataGenerator(rescale=1./255).flow_from_directory(val_path,
                                                                        target_size = (image_size,image_size),
                                                                        batch_size = batch_size,
                                                                        class_mode = 'binary')
test_set = ImageDataGenerator(rescale=1./255).flow_from_directory(val_path,
                                                                           target_size = (image_size,image_size),
                                                                           batch_size = batch_size,
                                                                           class_mode = 'binary',
                                                                           shuffle = False)

Found 200508 images belonging to 2 classes.
Found 17000 images belonging to 2 classes.
Found 17000 images belonging to 2 classes.


## Model

In [41]:
input_shape = (image_size, image_size, 3)
inputs = Input(input_shape)

xception = Xception(include_top = False, input_shape= input_shape)(inputs)
mobile_net = MobileNetV2(include_top = False, input_shape= input_shape)(inputs)

outputs = Concatenate(axis=-1)([GlobalAveragePooling2D()(xception), GlobalAveragePooling2D()(mobile_net)]) 
# concatenate function 
outputs = Dropout(0.5)(outputs)
outputs = Dense(1, activation='sigmoid')(outputs)

model = Model(inputs, outputs)
model.compile(optimizer=Adam(lr=0.0001, decay=0.00001),
              loss='binary_crossentropy',
              metrics=['accuracy'])
model.summary()


9406464/9406464 [==============================] - 1s 0us/step
Model: "model"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_1 (InputLayer)           [(None, 96, 96, 3)]  0           []                               
                                                                                                  
 xception (Functional)          (None, 3, 3, 2048)   20861480    ['input_1[0][0]']                
                                                                                                  
 mobilenetv2_1.00_96 (Functiona  (None, 3, 3, 1280)  2257984     ['input_1[0][0]']                
 l)                                                                                               
                                                                                                  
 global_average_pooling2d (Glob

C:\Users\super\anaconda3\lib\site-packages\keras\optimizers\optimizer_v2\adam.py:110: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super(Adam, self).__init__(name, **kwargs)


In [ ]:
history = model.fit_generator(train_set,
                              steps_per_epoch=len(train_set), 
                              validation_data=val_set,
                              validation_steps=len(val_set),
                              epochs=5,
                              verbose=1,
                              callbacks=PlotLossesKeras())

## Training

In [ ]:
# Training

history = model.fit_generator(train_set, 
                              validation_data=val_set,
                              steps_per_epoch=len(train_set)/batch_size ,
                              validation_steps=len(val_set)/batch_size, 
                              epochs = 15,
                              verbose = 1,
                              )

plt.plot(history.history['loss'])
plt.ylabel("loss")
plt.xlabel("epoch")
plt.title("Training Loss Curve")
plt.show()